# Final Project: Survival of The Fittest
## EPS 109
## Sarah Pedrami

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap
%matplotlib osx
    
## Function to display the matrix
def display(A):
    maxX = A.shape[0]
    maxY = A.shape[1]
    B = np.zeros((maxY, maxX))
    for ix in range(0,maxX):
        for iy in range(0,maxY):
            B[maxY-1-iy,ix] = A[ix,iy]

    plt.rcParams['figure.figsize'] = [6, 6/maxX*maxY]
    plt.imshow(B, cmap=c_map);
    plt.axis('off');
    plt.show()
    plt.draw()


## Self-created colormap to assign the colors grey to "rock", white to "paper", and tomato (red) to "scissors"
c_map = ListedColormap(["black", "grey", "white", "tomato"])

## Initial parameters for A, a 25x25 pixel box
maxX = 25
maxY = 25
A = np.zeros((maxX, maxY))
#display(A)

In [ ]:
## Initial number of pixels representing each object type; 60 in total
n_rock = 20
n_paper = 20
n_scissors = 20

## Function to populate the matrix A by randomly placing each particle within it
## Returns a matrix with the positions [x,y] of each particle
def populate(size, num):
    population = [[np.random.randint(0, maxX-1),np.random.randint(0,maxY-1)] for _ in range (size)]
    for i in range (size):
        A[population[i][0], population[i][1]] = num
    return population

#initial_rock = populate(n_rock, 1)
#initial_paper = populate(n_paper, 2)
#initial_scissors = populate(n_scissors, 3)

#display(A)

In [ ]:
## Function to simulate the movement of objects (pixels) via random walks
def move(data):
    newpos = data
    for i in range(0, len(data)):
        r = np.random.random()
        x0 = data[i][0]
        y0 = data[i][1]
        
        ## Move left
        if r <= 0.25:
            x = x0 - 1
            y = y0
        ## Move right
        elif r <= 0.5:
            x = x0 + 1
            y = y0
        ## Move up
        elif r <= 0.75:
            x = x0
            y = y0 + 1
        ## Move down
        elif r <= 1:
            x = x0
            y = y0 - 1

        newpos[i][0]= x
        newpos[i][1]= y
        
        ## Enforcing boundary conditions; pixels re-enter on the other side of the box if they exit the boundary
        
        if x >= maxX - 1:
            newpos[i][0] = x0
        if y >= maxY - 1:
            newpos[i][1] = y0
        if x <= 0:
            newpos[i][0] = x0
        if y <= 0:
            newpos[i][1] = y0

    return newpos

In [ ]:
## Function to find the neighboring pixels
## Returns an array containing the positions of the neighboring pixels
def findNeighbor(x,y):
    n1 = [x-1, y] ## Left neighbor
    n2 = [x+1, y] ## Right neighbor
    n3 = [x, y-1] ## Bottom neighbor
    n4 = [x, y+1] ## Top neighbor
    n5 = [x+1, y+1] ## Top-Right neighbor
    n6 = [x+1, y-1] ## Bottom-Right neighbor
    n7 = [x-1, y+1] ## Top-Left neighbor
    n8 = [x-1, y-1] ## Bottom-Left neighbor
    n9 = [x,y] ## Neighbor at the same location
    neighbors = [n1,n2,n3,n4,n5,n6,n7,n8,n9]
    neighbors =  [i for i in neighbors if 0<=i[0]<maxX and 0<=i[1]<maxY]
    return neighbors

In [ ]:
## Function to determine the object type of a pixel's neighbors
def findNeighbors_type(data):
    neighbor = []
    for i in range(0, len(data)):
        x = data[i][0]
        y = data[i][1]
        neighbor.append(findNeighbor(x,y))
    return neighbor

In [ ]:
## Function to reassign "captured" pixels to their updated object type (R->P, P->S, S->R)
## 1 = Rock, 2 = Paper, 3 = Scissors
def reassign(data):
    for i in range(0,len(data)):
        if A[data[i][0], data[i][1]] == 1:
            A[data[i][0], data[i][1]] = 2
        elif A[data[i][0], data[i][1]] == 2:
            A[data[i][0], data[i][1]] = 3
        elif A[data[i][0], data[i][1]] == 3:
            A[data[i][0], data[i][1]] = 1
    return data

In [ ]:
## Function to simulate the "spread" of one object type to another as pixels get "captured"
## Returns the updated positions and object types of the pixels
def spread(rock, paper, scissors):
    new_rock = rock
    new_paper = paper
    new_scissors = scissors
    neighbors_rock = findNeighbors_type(rock)
    neighbors_paper = findNeighbors_type(paper)
    neighbors_scissors = findNeighbors_type(scissors)
    
    ## Checks to see if any of the "rock" pixels have "scissors" neighbors. If so, the positions of
    ## each "scissors" neighbor is added to the "rock" array and removed from the "scissors" array.
    ## Essentially the "scissors" pixels become "rock" pixels. The statements for R->P and P->S 
    ## follow the same logic & implementation.
    for i in range(0, len(neighbors_rock)):
        for j in range(0, len(neighbors_rock[i])):
            for k in range (0, len(scissors)):
                if neighbors_rock[i][j] == scissors[k]:
                    new_rock.append(scissors[k])
                    scissors.pop(k)
                    break
                    
    for i in range(0, len(neighbors_paper)):
        for j in range(0, len(neighbors_paper[i])):
            for k in range (0, len(rock)):
                if neighbors_paper[i][j] == rock[k]:
                    new_paper.append(rock[k])
                    rock.pop(k)
                    break
                    
    for i in range(0, len(neighbors_scissors)):
        for j in range(0, len(neighbors_scissors[i])):
            for k in range (0, len(paper)):
                if neighbors_scissors[i][j] == paper[k]:
                    new_scissors.append(paper[k])
                    paper.pop(k)
                    break
                
            
    return reassign(new_rock), reassign(new_paper), reassign(new_scissors)

In [ ]:
## Over-arching function that calls the other previously-defined functions to simulate the movement of the pixels
## visually. Each of the particles are first moved before updating their corresponding object type if any "captures"
## took place. Then, the updated particle positions are transferred into a new matrix which is displayed 
## upon returning the function.
def movement_visual(new_rock, new_paper, new_scissors):
    updated_rock = move(new_rock)
    updated_paper = move(new_paper)
    updated_scissors = move(new_scissors)
    
    updated_rock_vis, updated_paper_vis, updated_scissors_vis = spread(updated_rock, updated_paper, updated_scissors)

    B = np.zeros((maxX, maxY))
    for i in range(0, len(updated_rock_vis)):
        B[updated_rock_vis[i][0], updated_rock_vis[i][1]] = 1
        
    for i in range(0, len(updated_paper_vis)):
        B[updated_paper_vis[i][0], updated_paper_vis[i][1]] = 2
        
    for i in range(0, len(updated_scissors_vis)):
        B[updated_scissors_vis[i][0], updated_scissors_vis[i][1]] = 3
        
    return display(B)

In [ ]:
## Function to check if any of the object types have "won", meaning all existing pixels in the box are of 
## that object type. If any objects have "won", the number corresponding to the object is returned
## (Recall that 1 = Rock, 2 = Paper, 3 = Scissors)
def check_win(rock, paper, scissors):
    winner = 0
    if len(rock) == 60:
        winner = 1
        print("Rock Wins")
    if len(paper) == 60:
        winner = 2
        print("Paper Wins")
    if len(scissors) == 60:
        winner = 3
        print("Scissors Wins")
    return winner

In [ ]:
## Animation parameters
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Final Animation', artist='Matplotlib',comment='Final Animation')
writer = FFMpegWriter(fps=8, metadata=metadata)
fig = plt.figure()


with writer.saving(fig, "animation.mp4", dpi=200):
    ## Sets the initial box conditions and size
    maxX = 25
    maxY = 25
    A = np.zeros((maxX, maxY))
    
    ## Populates the matrix A with 20 of each particle type
    n_rock = 20
    n_paper = 20
    n_scissors = 20

    initial_rock = populate(n_rock, 1)
    initial_paper = populate(n_paper, 2)
    initial_scissors = populate(n_scissors, 3)
    
    ## Variables to run the "while" loop and to keep track of each iteration 
    winner = 0
    count = 0
    
    ## Runs until there is a winner
    while winner == 0:
        ## Keeps track of the iteration number and the number of pixels of each object type
        print('Iteration:', count);
        print('Rock Count:', len(initial_rock), 'Paper Count:', len(initial_paper), 'Scissors Count:', len(initial_scissors), '\n')
        count += 1
        
        ## Updates each frame of the animation
        plt.plot()
        movement_visual(initial_rock, initial_paper, initial_scissors)
        
        ## Checks to see if any object has "won"
        winner = check_win(initial_rock, initial_paper, initial_scissors)
        
        writer.grab_frame()

---

In [ ]:
## Function to simulate one "game" of Rock Paper Scissors.
## Uses exact portions of the functions defined above, the only difference being that nothing is visually displayed.
def onegamesim():
    maxX = 25
    maxY = 25
    A = np.zeros((maxX, maxY))
    
    n_rock = 20
    n_paper = 20
    n_scissors = 20

    new_rock = populate(n_rock, 1)
    new_paper = populate(n_paper, 2)
    new_scissors = populate(n_scissors, 3)
    
    winner = 0
    
    while winner == 0:
        updated_rock = move(new_rock)
        updated_paper = move(new_paper)
        updated_scissors = move(new_scissors)

        new_rock, new_paper, new_scissors = spread(updated_rock, updated_paper, updated_scissors)
        
        if len(new_rock) == 60:
            winner = 1
        if len(new_paper) == 60:
            winner = 2
        if len(new_scissors) == 60:
            winner = 3

    return winner

In [ ]:
## Plays the game 300 times and stores the corresponding number of the winning object into an array
wins_arr = []
    
for i in range(300):
    result = onegamesim()
    wins_arr.append(result)

In [ ]:
%matplotlib inline

## Creates a histogram showing the frequency of the winning object. If our simulation is truly random, we expect
## to see a relatively even distribution of wins amongst the different object types.
plt.hist(wins_arr, bins=3, color='thistle', edgecolor='purple', linewidth=1.5)
plt.xticks(np.arange(1,4,1))
plt.title("Frequency of Wins Among The Objects, 300 Total Simulations")
plt.xlabel("Rock                         Paper                         Scissors")
plt.ylabel("Number of Wins")